In [9]:
import pandas as pd
import numpy as np
import seaborn as sns
import pyarrow
sns.set()
import gc
gc.collect()
import matplotlib.pyplot as plt  
%matplotlib inline
from tqdm import tqdm
tqdm.pandas()

from pyhive import presto
from datetime import datetime
from datetime import timedelta
import warnings
warnings.filterwarnings("ignore")
import math
from functools import reduce
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', 100)


In [15]:
conn = presto.connect(
    host="presto.processing.yoda.run",
    #host="bi-presto.serving.data.production.internal",
    #host="prime-trino.serving.data.production.internal",
    port=80,
    protocol="http",
    catalog="hive",
    username="manoj.kumar@rapido.bike",
)


def run_query(query):
    return pd.read_sql_query(query, conn)

In [18]:
d_query = f"""
SELECT 
    order_date,
    epoch,
    spd_fraud_flag,
    order_id,
    captain_id, 
    city_name,
    customer_id,
    captain_location_longitude,
    captain_location_latitude
FROM orders.order_logs_snapshot
WHERE 
    yyyymmdd between '20221201' and '20231231'
    and order_status = 'dropped'
    -- and spd_fraud_flag != True
    and captain_id in ( select distinct profile_identity from raw.clevertap_captain_events_master where yyyymmdd between '20221201 and '20231231' and regexp_like(eventProps,'"location_spoofing":"true"' and eventname = 'fraud_detection') 
    and service_obj_service_name in ('Link', 'Auto')

order by captain_id,order_date desc

"""
data = run_query(d_query)
data

DatabaseError: {'message': "line 17:20: mismatched input 'in'. Expecting: 'AND', 'EXCEPT', 'FETCH', 'GROUP', 'HAVING', 'INTERSECT', 'LIMIT', 'OFFSET', 'OR', 'ORDER', 'UNION', <EOF>", 'errorCode': 1, 'errorName': 'SYNTAX_ERROR', 'errorType': 'USER_ERROR', 'errorLocation': {'lineNumber': 17, 'columnNumber': 20}, 'failureInfo': {'type': 'io.trino.sql.parser.ParsingException', 'message': "line 17:20: mismatched input 'in'. Expecting: 'AND', 'EXCEPT', 'FETCH', 'GROUP', 'HAVING', 'INTERSECT', 'LIMIT', 'OFFSET', 'OR', 'ORDER', 'UNION', <EOF>", 'cause': {'type': 'org.antlr.v4.runtime.InputMismatchException', 'suppressed': [], 'stack': ['io.trino.sql.parser.SqlParser$2.recoverInline(SqlParser.java:122)', 'org.antlr.v4.runtime.Parser.match(Parser.java:206)', 'io.trino.sql.parser.SqlBaseParser.singleStatement(SqlBaseParser.java:263)', 'io.trino.sql.parser.SqlParser.invokeParser(SqlParser.java:139)', 'io.trino.sql.parser.SqlParser.createStatement(SqlParser.java:84)', 'io.trino.execution.QueryPrepa

In [58]:
data.to_csv('loc.csv',index=False)

In [60]:
def convert_to_datetime(epoch):
         
 base_datetime = datetime(1970, 1, 1,5,30)
 delta = timedelta(0, 0, 0, float(epoch))
 return base_datetime + delta

data['createdon'] = data[['epoch']].apply(lambda x: convert_to_datetime(x[0]), axis=1)
data

order_date          epoch  spd_fraud_flag                  order_id  \
0       2022-12-27  1672122639719           False  63aa910ec68b542c15d518f5   
1       2022-12-27  1672124994282           False  63aa9a41c68b5458e2d55c68   
2       2022-12-25  1671973925249           False  63a84c24d68e36695a0b3547   
3       2022-12-24  1671893745196           False  63a712f04c749459e5912774   
4       2022-12-24  1671897361224           False  63a72110f634933c8ef9db77   
...            ...            ...             ...                       ...   
461411  2023-01-04  1672842781722           False  63b58e1d0c92117d2b41480f   
461412  2023-01-03  1672701385709           False  63b365c964598c15de1c3176   
461413  2023-01-03  1672761972676           False  63b45274cad65e3a39c447ef   
461414  2023-01-03  1672713425321           False  63b394d1e45c8b0832603fb8   
461415  2023-01-03  1672703906079           False  63b36fa264598c15de1c375f   

                      captain_id    city_name               customer_id  \
0       5737caaeddbec220de03ed29    Bangalore  5acca139d266870cd1fd78ff   
1       5737caaeddbec220de03ed29    Bangalore  5acca139d266870cd1fd78ff   
2       5737caaeddbec220de03ed29    Bangalore  5acca139d266870cd1fd78ff   
3       5737caaeddbec220de03ed29    Bangalore  5acca139d266870cd1fd78ff   
4       5737caaeddbec220de03ed29    Bangalore  5acca139d266870cd1fd78ff   
...                          ...          ...                       ...   
461411  63b03404b3866496b78861fe  Bhubaneswar  63b57e4e6b2244fa2c939754   
461412  63b03404b3866496b78861fe  Bhubaneswar  5f04a15e4975ffc79b552da3   
461413  63b03404b3866496b78861fe  Bhubaneswar  63b4520f3be8e42b1d02467c   
461414  63b03404b3866496b78861fe  Bhubaneswar  62cd54369a526957df483d8c   
461415  63b03404b3866496b78861fe  Bhubaneswar  620bcc31257e92f4bed523af   

        captain_location_longitude  captain_location_latitude  \
0                        77.717110                  12.951600   
1                        77.709351                  12.953587   
2                        77.717255                  12.954992   
3                        77.724274                  12.960972   
4                        77.722618                  12.960531   
...                            ...                        ...   
461411                   85.828743                  20.297165   
461412                   85.803596                  20.328249   
461413                   85.826126                  20.295368   
461414                   85.788155                  20.257345   
461415                   85.793785                  20.271427   

                     createdon  
0      2022-12-27 12:00:39.719  
1      2022-12-27 12:39:54.282  
2      2022-12-25 18:42:05.249  
3      2022-12-24 20:25:45.196  
4      2022-12-24 21:26:01.224  
...                        ...  
461411 2023-01-04 20:03:01.722  
461412 2023-01-03 04:46:25.709  
461413 2023-01-03 21:36:12.676  
461414 2023-01-03 08:07:05.321  
461415 2023-01-03 05:28:26.079  

[461416 rows x 10 columns]

In [80]:
data['lagged_values_long'] = data.sort_values(by = ['epoch'],ascending = False).groupby(['captain_id'])['captain_location_longitude'].shift(1)
data['lagged_values_lat'] = data.sort_values(by = ['epoch'],ascending= False).groupby(['captain_id'])['captain_location_latitude'].shift(1)
data

order_date          epoch  spd_fraud_flag                  order_id  \
0       2022-12-27  1672122639719           False  63aa910ec68b542c15d518f5   
1       2022-12-27  1672124994282           False  63aa9a41c68b5458e2d55c68   
2       2022-12-25  1671973925249           False  63a84c24d68e36695a0b3547   
3       2022-12-24  1671893745196           False  63a712f04c749459e5912774   
4       2022-12-24  1671897361224           False  63a72110f634933c8ef9db77   
...            ...            ...             ...                       ...   
461411  2023-01-04  1672842781722           False  63b58e1d0c92117d2b41480f   
461412  2023-01-03  1672701385709           False  63b365c964598c15de1c3176   
461413  2023-01-03  1672761972676           False  63b45274cad65e3a39c447ef   
461414  2023-01-03  1672713425321           False  63b394d1e45c8b0832603fb8   
461415  2023-01-03  1672703906079           False  63b36fa264598c15de1c375f   

                      captain_id    city_name               customer_id  \
0       5737caaeddbec220de03ed29    Bangalore  5acca139d266870cd1fd78ff   
1       5737caaeddbec220de03ed29    Bangalore  5acca139d266870cd1fd78ff   
2       5737caaeddbec220de03ed29    Bangalore  5acca139d266870cd1fd78ff   
3       5737caaeddbec220de03ed29    Bangalore  5acca139d266870cd1fd78ff   
4       5737caaeddbec220de03ed29    Bangalore  5acca139d266870cd1fd78ff   
...                          ...          ...                       ...   
461411  63b03404b3866496b78861fe  Bhubaneswar  63b57e4e6b2244fa2c939754   
461412  63b03404b3866496b78861fe  Bhubaneswar  5f04a15e4975ffc79b552da3   
461413  63b03404b3866496b78861fe  Bhubaneswar  63b4520f3be8e42b1d02467c   
461414  63b03404b3866496b78861fe  Bhubaneswar  62cd54369a526957df483d8c   
461415  63b03404b3866496b78861fe  Bhubaneswar  620bcc31257e92f4bed523af   

        captain_location_longitude  captain_location_latitude  \
0                        77.717110                  12.951600   
1                        77.709351                  12.953587   
2                        77.717255                  12.954992   
3                        77.724274                  12.960972   
4                        77.722618                  12.960531   
...                            ...                        ...   
461411                   85.828743                  20.297165   
461412                   85.803596                  20.328249   
461413                   85.826126                  20.295368   
461414                   85.788155                  20.257345   
461415                   85.793785                  20.271427   

                     createdon  lagged_values_long  lagged_values_lat  \
0      2022-12-27 12:00:39.719           77.709351          12.953587   
1      2022-12-27 12:39:54.282                 NaN                NaN   
2      2022-12-25 18:42:05.249           77.717110          12.951600   
3      2022-12-24 20:25:45.196           77.724518          12.955233   
4      2022-12-24 21:26:01.224           77.717255          12.954992   
...                        ...                 ...                ...   
461411 2023-01-04 20:03:01.722           85.817871          20.300203   
461412 2023-01-03 04:46:25.709           85.793785          20.271427   
461413 2023-01-03 21:36:12.676           85.841446          20.267559   
461414 2023-01-03 08:07:05.321           85.826126          20.295368   
461415 2023-01-03 05:28:26.079           85.788155          20.257345   

        diff_long  diff_lat  flag  
0             NaN       NaN     0  
1       -0.007759  0.001987     0  
2        0.007904  0.001406     0  
3        0.007019  0.005980     0  
4       -0.001656 -0.000441     0  
...           ...       ...   ...  
461411   0.028526  0.045959     0  
461412  -0.025146  0.031084     0  
461413   0.022530 -0.032881     0  
461414  -0.037971 -0.038023     0  
461415   0.005630  0.014082     0  

[461416 rows x 15 columns]

In [81]:
data['diff_long']= data['captain_location_longitude']-data['lagged_values_long']
data['diff_lat']= data['captain_location_latitude']-data['lagged_values_lat']
data

order_date          epoch  spd_fraud_flag                  order_id  \
0       2022-12-27  1672122639719           False  63aa910ec68b542c15d518f5   
1       2022-12-27  1672124994282           False  63aa9a41c68b5458e2d55c68   
2       2022-12-25  1671973925249           False  63a84c24d68e36695a0b3547   
3       2022-12-24  1671893745196           False  63a712f04c749459e5912774   
4       2022-12-24  1671897361224           False  63a72110f634933c8ef9db77   
...            ...            ...             ...                       ...   
461411  2023-01-04  1672842781722           False  63b58e1d0c92117d2b41480f   
461412  2023-01-03  1672701385709           False  63b365c964598c15de1c3176   
461413  2023-01-03  1672761972676           False  63b45274cad65e3a39c447ef   
461414  2023-01-03  1672713425321           False  63b394d1e45c8b0832603fb8   
461415  2023-01-03  1672703906079           False  63b36fa264598c15de1c375f   

                      captain_id    city_name               customer_id  \
0       5737caaeddbec220de03ed29    Bangalore  5acca139d266870cd1fd78ff   
1       5737caaeddbec220de03ed29    Bangalore  5acca139d266870cd1fd78ff   
2       5737caaeddbec220de03ed29    Bangalore  5acca139d266870cd1fd78ff   
3       5737caaeddbec220de03ed29    Bangalore  5acca139d266870cd1fd78ff   
4       5737caaeddbec220de03ed29    Bangalore  5acca139d266870cd1fd78ff   
...                          ...          ...                       ...   
461411  63b03404b3866496b78861fe  Bhubaneswar  63b57e4e6b2244fa2c939754   
461412  63b03404b3866496b78861fe  Bhubaneswar  5f04a15e4975ffc79b552da3   
461413  63b03404b3866496b78861fe  Bhubaneswar  63b4520f3be8e42b1d02467c   
461414  63b03404b3866496b78861fe  Bhubaneswar  62cd54369a526957df483d8c   
461415  63b03404b3866496b78861fe  Bhubaneswar  620bcc31257e92f4bed523af   

        captain_location_longitude  captain_location_latitude  \
0                        77.717110                  12.951600   
1                        77.709351                  12.953587   
2                        77.717255                  12.954992   
3                        77.724274                  12.960972   
4                        77.722618                  12.960531   
...                            ...                        ...   
461411                   85.828743                  20.297165   
461412                   85.803596                  20.328249   
461413                   85.826126                  20.295368   
461414                   85.788155                  20.257345   
461415                   85.793785                  20.271427   

                     createdon  lagged_values_long  lagged_values_lat  \
0      2022-12-27 12:00:39.719           77.709351          12.953587   
1      2022-12-27 12:39:54.282                 NaN                NaN   
2      2022-12-25 18:42:05.249           77.717110          12.951600   
3      2022-12-24 20:25:45.196           77.724518          12.955233   
4      2022-12-24 21:26:01.224           77.717255          12.954992   
...                        ...                 ...                ...   
461411 2023-01-04 20:03:01.722           85.817871          20.300203   
461412 2023-01-03 04:46:25.709           85.793785          20.271427   
461413 2023-01-03 21:36:12.676           85.841446          20.267559   
461414 2023-01-03 08:07:05.321           85.826126          20.295368   
461415 2023-01-03 05:28:26.079           85.788155          20.257345   

        diff_long  diff_lat  flag  
0        0.007759 -0.001987     0  
1             NaN       NaN     0  
2        0.000145  0.003392     0  
3       -0.000244  0.005739     0  
4        0.005363  0.005539     0  
...           ...       ...   ...  
461411   0.010872 -0.003038     0  
461412   0.009811  0.056822     0  
461413  -0.015320  0.027809     0  
461414  -0.037971 -0.038023     0  
461415   0.005630  0.014082     0  

[461416 rows x 15 columns]

In [82]:
data.fillna(0)
data['flag'] = np.where(data['diff_lat']>2,1,np.where(data['diff_long']>2,1,0))
data1 = data[data.flag ==1]
data1

order_date          epoch  spd_fraud_flag                  order_id  \
23525   2023-03-07  1678180412791           False  6407003acae012fa0c294d73   
23700   2023-03-09  1678351858436           False  64099df172b134a05d0cc861   
109242  2023-03-05  1678040897736           False  6404df41effcf48dd4a7b970   
138134  2023-03-06  1678100430082           False  6405c7ccac2e1d1859efb54c   
164469  2023-02-24  1677181927314            True  63f7c3e7b9cd8c5194b3ab15   
215624  2023-03-20  1679321470726           False  6418697d988558955dbc9063   
215678  2023-03-05  1678019963198           False  64048d7a068a9c05655329aa   
251272  2023-03-23  1679567329871           False  641c29e0c134c40a812a81f4   
330851  2023-03-22  1679502648804           False  641b2d380982f984973e4062   
341701  2023-03-08  1678289974586           False  6408ac34068a9cbf835b78e0   
372264  2023-03-05  1677996256805           False  640430dfc6753a955e902737   
372266  2023-03-02  1677754177313           False  64007f40effcf47a8e9e154c   
382208  2023-01-01  1672576300883            True  63b17d2ccad65e3a39bef2a2   
382211  2023-01-01  1672573718702           False  63b1731664598c15de18bdab   
382366  2022-12-06  1670325105166           False  638f23712a233b34f62e80b9   
382373  2022-12-06  1670326552571            True  638f29189b4cab3de44e8c02   
382397  2022-12-03  1670071482130           False  638b44ba0479737506b7727b   
382400  2022-12-03  1670075121252            True  638b52f110e88d5b9aa5f6ea   
422243  2022-12-01  1669879877053           False  638858452a233b34f620fb8f   
433818  2022-12-02  1669976364042           False  6389d12c31c5e23aba36c683   
433828  2022-12-02  1669962079456           False  6389995fd1f95e048707b71b   
433842  2022-12-01  1669900510627           False  6388a8de1d5e0471e4b9c293   
433846  2022-12-01  1669906776418           False  6388c15848495c5c15c00c06   
448885  2023-03-08  1678264066757           False  640847029ed5b470f7fba234   
453318  2022-12-02  1669968159336           False  6389b11fd1f95e048707f73b   

                      captain_id   city_name               customer_id  \
23525   5bb731337e7bc30a3838b097      Jaipur  5acca139d266870cd1fd78ff   
23700   5bbc4f367e7bc30a3839e484      Jaipur  5acca139d266870cd1fd78ff   
109242  5d75d9326012fb46f2f85953      Jaipur  5acca139d266870cd1fd78ff   
138134  5df0d078732f142b5946ff23      Jaipur  5acca139d266870cd1fd78ff   
164469  5e60aaa42d7f4d189294e216    Guwahati  63f76806f4d98ae4ad77d03f   
215624  6039c04ba8c5b97ab7faa656      Jaipur  5acca139d266870cd1fd78ff   
215678  6039c04ba8c5b97ab7faa656      Jaipur  5acca139d266870cd1fd78ff   
251272  611afe638902095c5551acc2      Jaipur  5acca139d266870cd1fd78ff   
330851  622ae1601811dc1e8784b77a      Jaipur  5acca139d266870cd1fd78ff   
341701  624be33ac50351d719185538      Jaipur  5acca139d266870cd1fd78ff   
372264  629a3c2c6cc0d42062609aa8      Jaipur  5acca139d266870cd1fd78ff   
372266  629a3c2c6cc0d42062609aa8      Jaipur  5acca139d266870cd1fd78ff   
382208  62b2c2e885b58c0a60e4c776        Pune  638e41a9f34c214835ba16a6   
382211  62b2c2e885b58c0a60e4c776        Pune  638e59e8ae745b39dc7e6718   
382366  62b2c2e885b58c0a60e4c776        Pune  63663a1b9d21982ea32332a1   
382373  62b2c2e885b58c0a60e4c776        Pune  63656999d58af73ccce23b6b   
382397  62b2c2e885b58c0a60e4c776        Pune  63866c344c014e70e7b376a2   
382400  62b2c2e885b58c0a60e4c776        Pune  624f2ac8fc8d847575aceeaf   
422243  63077372d7ac6d5871e803dc  Vijayawada  5e11f6af39136622c07e8185   
433818  633206516b27ad8ba50ba1cf     Chennai  638904fc08087ff705a2a718   
433828  633206516b27ad8ba50ba1cf     Chennai  638958df6e950e449c402bf5   
433842  633206516b27ad8ba50ba1cf     Chennai  6388a89e7885e8b228d86d08   
433846  633206516b27ad8ba50ba1cf     Chennai  637dbb644036dd4f3635af6d   
448885  6364eb22677a28952c304d41   Gorakhpur  5d75f0c5d0286d106d811a7f   
453318  63788840ac81a611c7569860     Chennai  5d7e2d3ad0286d106d8ebdb9   

        captain_location_lon

In [83]:
flagged =  pd.DataFrame(data1['captain_id'].drop_duplicates())

flagged

captain_id
23525   5bb731337e7bc30a3838b097
23700   5bbc4f367e7bc30a3839e484
109242  5d75d9326012fb46f2f85953
138134  5df0d078732f142b5946ff23
164469  5e60aaa42d7f4d189294e216
215624  6039c04ba8c5b97ab7faa656
251272  611afe638902095c5551acc2
330851  622ae1601811dc1e8784b77a
341701  624be33ac50351d719185538
372264  629a3c2c6cc0d42062609aa8
382208  62b2c2e885b58c0a60e4c776
422243  63077372d7ac6d5871e803dc
433818  633206516b27ad8ba50ba1cf
448885  6364eb22677a28952c304d41
453318  63788840ac81a611c7569860

In [84]:
data2 = data.merge(flagged,on='captain_id',how='right')
data2

order_date          epoch  spd_fraud_flag                  order_id  \
0     2023-04-02  1680417528356           False  642922f72c451096b872e863   
1     2023-04-02  1680424547292           False  64293e613e19cd81656466b9   
2     2023-04-02  1680422830978           False  642937ae3e19cdb73f644abe   
3     2023-04-01  1680354204051           False  64282b99d8057442f2d1f634   
4     2023-04-01  1680331718732           False  6427d3c4f3a9ba02e389d53b   
5     2023-04-01  1680328742159           False  6427c825f3a9ba15ef89c53d   
6     2023-04-01  1680333954455           False  6427dc810a0576a2b0ad1ee7   
7     2023-04-01  1680341252575           False  6427f8fc928e35f29ca136ee   
8     2023-04-01  1680335867444           False  6427e3fac569851ba78406b9   
9     2023-04-01  1680348831913           False  6428169f89fb5282b85b9fc1   
10    2023-04-01  1680338196857           False  6427ed13b760627fc5ec9200   
11    2023-03-31  1680258785754           False  6426b6e0080acd2706239b91   
12    2023-03-31  1680247171378           False  6426898189fb527962587139   
13    2023-03-31  1680276861205           False  6426fd7955557d82d3154b84   
14    2023-03-31  1680266005824           False  6426d3154cd5c37c330ae259   
15    2023-03-31  1680250781780           False  6426979d60fd9f9134ff2bac   
16    2023-03-31  1680270469204           False  6426e484418c8b69265656e3   
17    2023-03-31  1680262255655           False  6426c46f080acd157123adc8   
18    2023-03-31  1680245514986           False  6426830955557d162813e3a8   
19    2023-03-31  1680253719554           False  6426a317faa66dc01337e668   
20    2023-03-29  1680077398460           False  6423f25555557d03040fb815   
21    2023-03-29  1680081874276           False  642403cd080acdf06e1f2079   
22    2023-03-29  1680072011914           False  6423dd4a8336481c431401cd   
23    2023-03-29  1680083727486           False  64240b0e9c052ef060424d62   
24    2023-03-29  1680074404399           False  6423e6a3f753d1c9366d9676   
25    2023-03-28  1679991845782           False  6422a4250c45a2f0e47b7a06   
26    2023-03-28  1679990384619           False  64229e6f70d04224ae30b47a   
27    2023-03-28  1679983964371           False  6422855b59dd5305984262b3   
28    2023-03-28  1679993791232           False  6422abbebe3ec557b4f7129f   
29    2023-03-28  1679979674552           False  642274990c45a20d6d7b23ea   
30    2023-03-28  1679985583262           False  64228baec6159e58b173a00a   
31    2023-03-28  1680004561859           False  6422d5d1928e3524b09820c4   
32    2023-03-28  1680002571704           False  6422ce0b0982f92ca94b972c   
33    2023-03-28  1679987738840           False  64229419305d0ec59d72cd8e   
34    2023-03-27  1679927416041           False  6421a876915362380872613d   
35    2023-03-27  1679894357186           False  642127533064d8cd6fd4dd4c   
36    2023-03-27  1679902300693           False  6421465bd1f56c5c3b4cb67a   
37    2023-03-27  1679914235608           False  642174f370d0427aa22ed8ee   
38    2023-03-27  1679897033071           False  642131c773ffe3dfda43e046   
39    2023-03-27  1679906879061           False  6421583eedd1419415af4540   
40    2023-03-27  1679917203217           False  64218092305d0eee96712507   
41    2023-03-27  1679919411744           False  64218933305d0ed817713332   
42    2023-03-27  1679903813036           False  64214c4491536219a8719bcc   
43    2023-03-27  1679899569646           False  64213bafc134c4131033dc36   
44    2023-03-27  1679908421319           False  64215e449a2f318194dfcdbd   
45    2023-03-27  1679911192958           False  64216918c0308c10f4f32e74   
46    2023-03-27  1679926479359           False  6421a4cec134c44dc034c5c8   
47    2023-03-26  1679826773407           False  64201f537087c178e46d073d   
48    2023-03-26  1679814822754           False  641ff0a4305d0e99e46ddcf8   
49    2023-03-26  1679807302435           False  641fd3458a20b1149af7900b   
50    2023-03-26  1679817741394           False  641ffc0b70d042f36c2bd49f   
51

In [85]:
data2 = data2.sort_values(by=['captain_id']).sort_values(by = ['epoch'],ascending = False)
pd.set_option('display.max_rows', 3000)
data2

order_date          epoch  spd_fraud_flag                  order_id  \
993   2023-04-03  1680516161896           False  642aa43f080acd55b42b5ff6   
994   2023-04-03  1680509597915           False  642a8a9b4efb4b555b3db4be   
995   2023-04-03  1680501982302           False  642a6cdd928e35005aa60e3d   
1000  2023-04-02  1680436527685           False  64296d2df3a9baceb08d742e   
998   2023-04-02  1680427700425           False  64294ab3928e35dfa5a414d9   
1     2023-04-02  1680424547292           False  64293e613e19cd81656466b9   
996   2023-04-02  1680422906339           False  642937f9d80574a6dcd43139   
2     2023-04-02  1680422830978           False  642937ae3e19cdb73f644abe   
997   2023-04-02  1680420048673           False  64292ccf89fb5201255dd056   
0     2023-04-02  1680417528356           False  642922f72c451096b872e863   
999   2023-04-02  1680417225228           False  642921c7faa66d02f93cba3a   
498   2023-04-01  1680365970905           False  642859919c052ecffd4a7b2d   
494   2023-04-01  1680362667332           False  64284caa85e2cb3f4aaadf42   
497   2023-04-01  1680359651392           False  642840e2418c8b15a0592d2e   
492   2023-04-01  1680355321664           False  64282ff8faa66d78cf3ae396   
3     2023-04-01  1680354204051           False  64282b99d8057442f2d1f634   
493   2023-04-01  1680349211703           False  6428181b3f824df541ab4938   
9     2023-04-01  1680348831913           False  6428169f89fb5282b85b9fc1   
495   2023-04-01  1680345144138           False  6428083655557d54981706ca   
496   2023-04-01  1680342486405           False  6427fdd5d80574cdd8d1a88a   
7     2023-04-01  1680341252575           False  6427f8fc928e35f29ca136ee   
10    2023-04-01  1680338196857           False  6427ed13b760627fc5ec9200   
8     2023-04-01  1680335867444           False  6427e3fac569851ba78406b9   
6     2023-04-01  1680333954455           False  6427dc810a0576a2b0ad1ee7   
4     2023-04-01  1680331718732           False  6427d3c4f3a9ba02e389d53b   
5     2023-04-01  1680328742159           False  6427c825f3a9ba15ef89c53d   
1303  2023-03-31  1680277863988           False  6427016555557d3aed156259   
13    2023-03-31  1680276861205           False  6426fd7955557d82d3154b84   
1302  2023-03-31  1680270633855           False  6426e52968e63cee926cbf03   
16    2023-03-31  1680270469204           False  6426e484418c8b69265656e3   
14    2023-03-31  1680266005824           False  6426d3154cd5c37c330ae259   
17    2023-03-31  1680262255655           False  6426c46f080acd157123adc8   
11    2023-03-31  1680258785754           False  6426b6e0080acd2706239b91   
19    2023-03-31  1680253719554           False  6426a317faa66dc01337e668   
15    2023-03-31  1680250781780           False  6426979d60fd9f9134ff2bac   
12    2023-03-31  1680247171378           False  6426898189fb527962587139   
18    2023-03-31  1680245514986           False  6426830955557d162813e3a8   
1308  2023-03-30  1680185199685           False  6425976f080acd2edb21cdd1   
1304  2023-03-30  1680183080545           False  64258f27f3a9ba4e4685dcd5   
1305  2023-03-30  1680180554365           False  64258548418c8bcaea53faaa   
1306  2023-03-30  1680178692092           False  64257e039c052e1c2644b326   
1307  2023-03-30  1680174487586           False  64256d96954a094e81ebaffd   
1001  2023-03-30  1680171317171           False  642561349c052e7ec44486ea   
1003  2023-03-30  1680169020714           False  6425583be6dcd6cf6a1cbc73   
1002  2023-03-30  1680164423507           False  64254646928e35d3739c318a   
504   2023-03-29  1680111552127           False  642477bfc51ecc69f17e75fc   
501   2023-03-29  1680107775786           False  642468ffc51ecca5137e4816   
499   2023-03-29  1680105578966           False  6424606aea9971c5f3cfd27c   
500   2023-03-29  1680100095626           False  64244afec51eccdc8d7db3ee   
1010  2023-03-29  1680099907078           False  64244a4202f103c9109feb89   
1006  2023-03-29  1680098586443           False  64244518e373333d1eaec83e   
50